# Capstone Project: BRICS Analysis Cleaning
## By Ryan Kidd

# Cleaning
After preparing the data in the first notebook, this notebook is designed to show the different cleaning procedures I will implement for my BRICS analysis. I have outlined several aspects throughout the 5 different datasets from `https://www.kaggle.com/docstein/brics-world-bank-indicators` that need to be cleaned in order for me to conduct different classification, machine learning, and statistical models. I will list them below.

- Check the formatting of the way the data is represented and ensure that the variable types are correct.
- Find the proportion of missing values per column and decide which columns need to be dropped and which can be imputed.
- Getting rid of all NaN/null values and removing columns that have a high proportion of missing data.
- For the columns that are missing approximately 10% of the data, I can impute the values by taking the mean of the next value and past value as the data is time series data.
- Finally, join all the 5 cleaned datasets together for the EDA

Next, I will load in the necessary packages for the cleaning process below.

In [2]:
# Import data science packages for Data Preparation, Cleaning, and Exploratory Data Analysis (EDA)
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
pd.set_option('display.max_rows', 500) # I needed to change the number of rows outputted because I have a large number of columns.

For the purpose of understanding how I transformed the datasets in the data preparation section, I have condensed the steps taken below. I will not use these dataframes as the Data Preparation section analyzed and discussed the steps throughout the notebook. This code is here as a reference.

In [3]:
# Reading in all of the CSV files Kaggle for BRICS analysis
df_economy = pd.read_csv('data/Economy_Data.csv', sep=';', index_col=0) # Had to add sep = ";" as all of the CSV file columns were separated with a ";" 
df_education = pd.read_csv('data/Education_And_Environ_Data.csv', sep=';', index_col=0) # Got rid of the index_column as it provides no useful information
df_public = pd.read_csv('data/Public_Sector_Indicators.csv', sep=';', index_col=0)
df_private = pd.read_csv('data/Private_Sector_Data.csv', sep=';', index_col=0)
df_health = pd.read_csv('data/Health_And_Poverty_Data.csv', sep=';', index_col=0)

# Removing all of the SeriesCode columns from the dataset
df_economy = df_economy.drop(['SeriesCode'], axis=1)
df_education = df_education.drop(['SeriesCode'], axis=1)
df_public = df_public.drop(['SeriesCode'], axis=1)
df_private = df_private.drop(['SeriesCode'], axis=1)
df_health = df_health.drop(['SeriesCode'], axis=1)

# Pivoting the dataframes for the cleaning
df_economy_reshape = pd.pivot_table(df_economy, values = 'Value', index = ['CountryName','CountryCode','Year'], columns = 'SeriesName')
df_education_reshape = pd.pivot_table(df_education, values = 'Value', index = ['CountryName','CountryCode','Year'], columns = 'SeriesName')
df_public_reshape = pd.pivot_table(df_public, values = 'Value', index = ['CountryName','CountryCode','Year'], columns = 'SeriesName')
df_private_reshape = pd.pivot_table(df_private, values = 'Value', index = ['CountryName','CountryCode','Year'], columns = 'SeriesName')
df_health_reshape = pd.pivot_table(df_health, values = 'Value', index = ['CountryName','CountryCode','Year'], columns = 'SeriesName')

In [4]:
# Reading in all of the CSV files created from the Data Preparation section
df_economyR = pd.read_csv('data/Economy_Rotated.csv') # When reading in new dataframes pandas automatically makes a indexer column 
df_educationR = pd.read_csv('data/Education_Rotated.csv') # I will need to keep the indexer_column for the cleaning process to look at the CountryName columns
df_publicR = pd.read_csv('data/Public_Rotated.csv') # Further, this removes the SeriesName that was added due to pivot_table.
df_privateR = pd.read_csv('data/Private_Rotated.csv')
df_healthR = pd.read_csv('data/Health_Rotated.csv')

### Economy Dataset Cleaning
In this section, I the economical indicator data that had the lowet proportion of missing values seen in the data preparation section. Further, the target variable `GDP Growth %Annual` is present in this dataset, which I will have to make sure that it is a good variable for analysis.

In [5]:
# Taking a look at the original dataframe
print(f'The current shape of the dataset: {df_economyR.shape}')
df_economyR.head(10)

The current shape of the dataset: (250, 335)


CountryName CountryCode    Year  \
0      Brazil         BRA  1970.0   
1      Brazil         BRA  1971.0   
2      Brazil         BRA  1972.0   
3      Brazil         BRA  1973.0   
4      Brazil         BRA  1974.0   
5      Brazil         BRA  1975.0   
6      Brazil         BRA  1976.0   
7      Brazil         BRA  1977.0   
8      Brazil         BRA  1978.0   
9      Brazil         BRA  1979.0   

   Adjusted net national income (annual % growth)  \
0                                             NaN   
1                                       11.642225   
2                                       12.379004   
3                                       12.214610   
4                                        5.160031   
5                                        2.928050   
6                                       13.847055   
7                                        6.897196   
8                                        1.727041   
9                                        6.489032   

   Adjusted net national income (constant 2010 US$)  \
0                                      3.918974e+11   
1                                      4.375230e+11   
2                                      4.916840e+11   
3                                      5.517413e+11   
4                                      5.802113e+11   
5                                      5.972002e+11   
6                                      6.798948e+11   
7                                      7.267885e+11   
8                                      7.393404e+11   
9                                      7.873164e+11   

   Adjusted net national income (current US$)  \
0                                3.786021e+10   
1                                4.414620e+10   
2                                5.252340e+10   
3                                7.058820e+10   
4                                9.341705e+10   
5                                1.086838e+11   
6                                1.336018e+11   
7                                1.544139e+11   
8                                1.743500e+11   
9                                1.936141e+11   

   Adjusted net national income per capita (annual % growth)  \
0                                                NaN           
1                                           8.928380           
2                                           9.704598           
3                                           9.580841           
4                                           2.702725           
5                                           0.518431           
6                                          11.177201           
7                                           4.392284           
8                                          -0.655074           
9                                           3.998180           

   Adjusted net national income per capita (constant 2010 US$)  \
0                                        4120.323413             
1                                        4488.201546             
2                                        4923.763456             
3                                        5395.501408             
4                                        5541.326994             
5                                        5570.054972             
6                                        6192.631217             
7                                        6464.629179             
8                                        6422.281063             
9                                        6679.055398             

   Adjusted net national income per capita (current US$)  \
0                                         398.053948       
1                                         452.860827       
2                                         525.973644       
3                                         690.284997       
4                                         892.182583       
5                                        1013.688084       
6           

Now with all of the dataframes loaded into the notebook, I can conduct the cleaning process according to the outline above. For this cleaning, I will first clean each dataframe, combining them at the end for the EDA. The first step includes checking the datatypes and formatting of the data represented in this dataset.

In [6]:
# Checking the number of columns that are type float64 and the size of the dataset, there should be 333 features that are type float64.
float_columns = df_economyR.select_dtypes(['float64']).columns
print(f'The number of numeric type columns: {len(float_columns)}')
print(f'The shape of the economy dataframe: {df_economyR.shape}')
df_economyR.dtypes # To show that the only datatypes that are string are CountryName and CountryCode

The number of numeric type columns: 333
The shape of the economy dataframe: (250, 335)


CountryName                                                                                          object
CountryCode                                                                                          object
Year                                                                                                float64
Adjusted net national income (annual % growth)                                                      float64
Adjusted net national income (constant 2010 US$)                                                    float64
Adjusted net national income (current US$)                                                          float64
Adjusted net national income per capita (annual % growth)                                           float64
Adjusted net national income per capita (constant 2010 US$)                                         float64
Adjusted net national income per capita (current US$)                                               float64
Adjusted net savings, exclud

I can see that the number of features went up from 332 to 335 from the previous dataframe in the last notebook. The number of columns is correct as when I pivoted the dataframe, the pivot considered the columns (CountryName, and Country Code) as an Index, not a feature and the Indexer was removed. With all columns added back into the dataframe, the total number of columns should be 335. The fact that many of the features are type float64 is a good sign as we do not have to change many columns besides the CountryName and CountryCode for machine learning purposes. For the next step of the cleaning process, I want to look at all the proportion of missing values in the dataframe features to ensure I clean everything.

In [7]:
# Checking to see if the length of the dataframe is the same as the shape method
len(df_economyR)

250

In [8]:
# Checking the number of null values by column
df_economyR.isna().sum()

CountryName                                                                                           0
CountryCode                                                                                           0
Year                                                                                                  0
Adjusted net national income (annual % growth)                                                       58
Adjusted net national income (constant 2010 US$)                                                     53
Adjusted net national income (current US$)                                                           28
Adjusted net national income per capita (annual % growth)                                            58
Adjusted net national income per capita (constant 2010 US$)                                          53
Adjusted net national income per capita (current US$)                                                28
Adjusted net savings, excluding particulate emission damage (% o

In [9]:
# Getting the proportion of missing values by column, I used .mean as essentially I am taking the average * 100.0
proportion = df_economyR.isna().mean()*100
proportion #print(df_economyR.isna().sum()/len(df_economyR)*100)

CountryName                                                                                          0.0
CountryCode                                                                                          0.0
Year                                                                                                 0.0
Adjusted net national income (annual % growth)                                                      23.2
Adjusted net national income (constant 2010 US$)                                                    21.2
Adjusted net national income (current US$)                                                          11.2
Adjusted net national income per capita (annual % growth)                                           23.2
Adjusted net national income per capita (constant 2010 US$)                                         21.2
Adjusted net national income per capita (current US$)                                               11.2
Adjusted net savings, excluding particulate emission da

From the results above, I can see that many of the columns have a high proportion of missing values. Considering these datasets are time series data and the value from the past year and next year can determine a majority of the missing values through imputing, I decided a threshold of 10% of the missing values can be imputed. Now, I will filter the dataset by columns to return columns with less than 10% of missing values.

In [10]:
print(f'The shape of the dataset after filtering: {df_economyR.loc[:, proportion <= 10.0].shape}')
df_economy_filter = df_economyR.loc[:, proportion <= 10.0]
df_economy_filter

The shape of the dataset after filtering: (250, 76)


CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

I can see that with the filtering technique, I am able to slice the dataset according to the proportion of missing data seen in the features with less than or equal to 10% of the total values. Now I have reduced the dataframe from 335 features to 76 features that I will need to fill in the NaN values with the available data.

In [11]:
# Filling in NaN values by Grouping by the CountryName column and transforming it in order to fillna by specific country mean values
df_economy_fill = df_economy_filter.groupby('CountryName').transform(lambda x: x.fillna(x.mean()))
print(f'The shape of the filled dataset: {df_economy_fill.shape}')
df_economy_fill # I will have to add in the CountryName and CountryCode columns to the combined dataset.

The shape of the filled dataset: (250, 74)


Year  Adjusted savings: carbon dioxide damage (% of GNI)  \
0    1970.0                                           0.372691    
1    1971.0                                           0.378426    
2    1972.0                                           0.379821    
3    1973.0                                           0.354143    
4    1974.0                                           0.323506    
5    1975.0                                           0.328014    
6    1976.0                                           0.296894    
7    1977.0                                           0.296063    
8    1978.0                                           0.313108    
9    1979.0                                           0.332934    
10   1980.0                                           0.357798    
11   1981.0                                           0.333266    
12   1982.0                                           0.345343    
13   1983.0                                           0.499338    
14   1984.0                                           0.524224    
15   1985.0                                           0.558641    
16   1986.0                                           0.530679    
17   1987.0                                           0.529146    
18   1988.0                                           0.507813    
19   1989.0                                           0.392948    
20   1990.0                                           0.408748    
21   1991.0                                           0.348696    
22   1992.0                                           0.554267    
23   1993.0                                           0.562213    
24   1994.0                                           0.493612    
25   1995.0                                           0.392491    
26   1996.0                                           0.415594    
27   1997.0                                           0.444765    
28   1998.0                                           0.498555    
29   1999.0                                           0.776124    
30   2000.0                                           0.747165    
31   2001.0                                           0.951648    
32   2002.0                                           1.080892    
33   2003.0                                           0.996788    
34   2004.0                                           0.921713    
35   2005.0                                           0.754987    
36   2006.0                                           0.643022    
37   2007.0                                           0.561133    
38   2008.0                                           0.519789    
39   2009.0                                           0.518514    
40   2010.0                                           0.470395    
41   2011.0                                           0.434845    
42   2012.0                                           0.517800    
43   2013.0                                           0.573253    
44   2014.0                                           0.644740    
45   2015.0                                           0.864867    
46   2016.0                                           0.830430    
47   2017.0                                           0.781795    
48   2018.0                                           0.940704    
49   2019.0                                           0.542946    
50   1970.0                                           1.382085    
51   1971.0                                           1.576715    
52   1972.0                                           1.580489    
53   1973.0                                           1.464952    
54   1974.0                                           1.612143    
55   1975.0                                           1.855925    
56   1976.0                                           2.235697    
57   1977.0                                           2.357602    
58   1978.0                                           

I can see the imputation worked, however the columns CountryName and CountryCode were removed as a result of the filling as they are object variables that cannot have their mean taken. I will need to add these columns for the finished dataframe. Thus, I store the two removed columns under a new dataframe, which I can insert later.

In [72]:
# Creating a dataframe for the CountryName and CountryCode columns for insertion at the end
df_insert1 = df_economy_filter['CountryName']
df_insert2 = df_economy_filter['CountryCode']
df_insert = pd.concat([df_insert1, df_insert2], axis=1)
df_insert

CountryName CountryCode
0                Brazil         BRA
1                Brazil         BRA
2                Brazil         BRA
3                Brazil         BRA
4                Brazil         BRA
5                Brazil         BRA
6                Brazil         BRA
7                Brazil         BRA
8                Brazil         BRA
9                Brazil         BRA
10               Brazil         BRA
11               Brazil         BRA
12               Brazil         BRA
13               Brazil         BRA
14               Brazil         BRA
15               Brazil         BRA
16               Brazil         BRA
17               Brazil         BRA
18               Brazil         BRA
19               Brazil         BRA
20               Brazil         BRA
21               Brazil         BRA
22               Brazil         BRA
23               Brazil         BRA
24               Brazil         BRA
25               Brazil         BRA
26               Brazil         BRA
27               Brazil         BRA
28               Brazil         BRA
29               Brazil         BRA
30               Brazil         BRA
31               Brazil         BRA
32               Brazil         BRA
33               Brazil         BRA
34               Brazil         BRA
35               Brazil         BRA
36               Brazil         BRA
37               Brazil         BRA
38               Brazil         BRA
39               Brazil         BRA
40               Brazil         BRA
41               Brazil         BRA
42               Brazil         BRA
43               Brazil         BRA
44               Brazil         BRA
45               Brazil         BRA
46               Brazil         BRA
47               Brazil         BRA
48               Brazil         BRA
49               Brazil         BRA
50                China         CHN
51                China         CHN
52                China         CHN
53                China         CHN
54                China         CHN
55                China         CHN
56                China         CHN
57                China         CHN
58                China         CHN
59                China         CHN
60                China         CHN
61                China         CHN
62                China         CHN
63                China         CHN
64                China         CHN
65                China         CHN
66                China         CHN
67                China         CHN
68                China         CHN
69                China         CHN
70                China         CHN
71                China         CHN
72                China         CHN
73                China         CHN
74                China         CHN
75                China         CHN
76                China         CHN
77                China         CHN
78                China         CHN
79                China         CHN
80                China         CHN
81                China         CHN
82                China         CHN
83                China         CHN
84                China         CHN
85                China         CHN
86                China         CHN
87                China         CHN
88                China         CHN
89                China         CHN
90                China         CHN
91                China         CHN
92                China         CHN
93                China         CHN
94                China         CHN
95                China         CHN
96                China         CHN
97                China         CHN
98                China         CHN
99                China         CHN
100               India         IND
101               India         IND
102               India         IND
103               India         IND
104               India         IND
105               India         IND
106               India         IND
107               India         IND
108               India         IND
109               India         IND
110             

In [76]:
# In order to add these columns back into the dataframe I used insert to manually do so.
#df_economy_fill.insert(0, 'CountryName', df_insert1) # The insert methods must be uncommented to add the two columns to the dataset
#df_economy_fill.insert(1, 'CountryCode', df_insert2)
#df_economy_fill = df_economy_fill.drop('CountryName',axis=1) #this was used to make sure the position of the column was correct
df_economy_fill

CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

In [77]:
# Check to see if imputation worked and no null values/duplicated rows
print(f'The shape of the cleaned dataset: {df_economy_fill.shape}')
print(f'Check to see if there are duplicated data: {df_economy_fill.duplicated().sum()/df_economy_fill.shape[0]*100.0} percent')
df_economy_fill.isna().sum()

The shape of the cleaned dataset: (250, 76)
Check to see if there are duplicated data: 0.0 percent


CountryName                                                            0
CountryCode                                                            0
Year                                                                   0
Adjusted savings: carbon dioxide damage (% of GNI)                     0
Adjusted savings: carbon dioxide damage (current US$)                  0
Adjusted savings: consumption of fixed capital (% of GNI)              0
Adjusted savings: consumption of fixed capital (current US$)           0
Adjusted savings: education expenditure (% of GNI)                     0
Adjusted savings: education expenditure (current US$)                  0
Adjusted savings: energy depletion (% of GNI)                          0
Adjusted savings: energy depletion (current US$)                       0
Adjusted savings: mineral depletion (% of GNI)                         0
Adjusted savings: mineral depletion (current US$)                      0
Agriculture, forestry, and fishing, value added (% 

With the first dataset cleaned and prepared for the EDA, now I will continue in the same steps for the rest of the 4 datasets.
### Education Dataset
Next, I will clean the education data that provides insight on different aspects related to human resource development in the BRICS countries.

In [27]:
# Taking a look at the original dataframe
print(f'The current shape of the dataset: {df_educationR.shape}')
df_educationR.head(10)

The current shape of the dataset: (250, 288)


CountryName CountryCode    Year  \
0      Brazil         BRA  1970.0   
1      Brazil         BRA  1971.0   
2      Brazil         BRA  1972.0   
3      Brazil         BRA  1973.0   
4      Brazil         BRA  1974.0   
5      Brazil         BRA  1975.0   
6      Brazil         BRA  1976.0   
7      Brazil         BRA  1977.0   
8      Brazil         BRA  1978.0   
9      Brazil         BRA  1979.0   

   Access to clean fuels and technologies for cooking (% of population)  \
0                                                NaN                      
1                                                NaN                      
2                                                NaN                      
3                                                NaN                      
4                                                NaN                      
5                                                NaN                      
6                                                NaN                      
7                                                NaN                      
8                                                NaN                      
9                                                NaN                      

   Access to electricity (% of population)  \
0                                      NaN   
1                                      NaN   
2                                      NaN   
3                                      NaN   
4                                      NaN   
5                                      NaN   
6                                      NaN   
7                                      NaN   
8                                      NaN   
9                                      NaN   

   Access to electricity, rural (% of rural population)  \
0                                                NaN      
1                                                NaN      
2                                                NaN      
3                                                NaN      
4                                                NaN      
5                                                NaN      
6                                                NaN      
7                                                NaN      
8                                                NaN      
9                                                NaN      

   Access to electricity, urban (% of urban population)  \
0                                                NaN      
1                                                NaN      
2                                                NaN      
3                                                NaN      
4                                                NaN      
5                                                NaN      
6                                                NaN      
7                                                NaN      
8                                                NaN      
9                                                NaN      

   Adjusted net enrollment rate, primary (% of primary school age children)  \
0                                                NaN                          
1                                                NaN                          
2                                                NaN                          
3                                                NaN                          
4                                                NaN                          
5                                                NaN                          
6                                                NaN                          
7                                                NaN                          
8                                                NaN                          
9                                                NaN                          

   Adjusted net enrollment rate, primary, female (% of primary school age children)  \
0   

From the initial look into the education dataset, I notice that the number of NaN values seems higher than the economy dataset. This was proven in the data preparation section, and I will now address how I want to proceed with the data cleaning. The first step is to check the datatypes of the features.

In [28]:
# Checking the number of columns that are type float64 and the size of the dataset
float_columns = df_educationR.select_dtypes(['float64']).columns
print(f'The number of numeric type columns: {len(float_columns)}')
print(f'The shape of the education dataframe: {df_educationR.shape}')
df_educationR.dtypes # To show that the only datatypes that are string are CountryName and CountryCode

The number of numeric type columns: 286
The shape of the education dataframe: (250, 288)


CountryName                                                                                                                           object
CountryCode                                                                                                                           object
Year                                                                                                                                 float64
Access to clean fuels and technologies for cooking (% of population)                                                                 float64
Access to electricity (% of population)                                                                                              float64
Access to electricity, rural (% of rural population)                                                                                 float64
Access to electricity, urban (% of urban population)                                                                                 float64
Adjusted net 

In [29]:
# Checking to see if the length of the dataframe is the same as the shape method
len(df_educationR)

250

The same principle applies with the datatype analysis of the economy dataset. There should be two less numeric type columns as CountryName and CountryCode are type objects. This aligns with the previous analysis explanation and I will now move on to checking for null values within each feature.

In [30]:
# Checking the number of null values by column
df_educationR.isna().sum()

CountryName                                                                                                                            0
CountryCode                                                                                                                            0
Year                                                                                                                                   0
Access to clean fuels and technologies for cooking (% of population)                                                                 165
Access to electricity (% of population)                                                                                              124
Access to electricity, rural (% of rural population)                                                                                 124
Access to electricity, urban (% of urban population)                                                                                 124
Adjusted net enrollment rate, primary (% 

In [31]:
# Getting the proportion of missing values by column, I used .mean as essentially I am taking the average * 100.0
proportion1 = df_educationR.isna().mean()*100
proportion1 #print(df_educationR.isna().sum()/len(df_educationR)*100)

CountryName                                                                                                                           0.0
CountryCode                                                                                                                           0.0
Year                                                                                                                                  0.0
Access to clean fuels and technologies for cooking (% of population)                                                                 66.0
Access to electricity (% of population)                                                                                              49.6
Access to electricity, rural (% of rural population)                                                                                 49.6
Access to electricity, urban (% of urban population)                                                                                 49.6
Adjusted net enrollment rate, prim

Looking at the proportion of null values throughout the dataset, I can tell that this dataset will have more columns dropped compared to the previous one if I set the proportion of missing values to 10%. Since many of these features have a high proportion of missing data present, they cannot be imputed and used in the EDA as the results will become skewed towards the mean. Next, I will set the threshold and use the filtering technique to slice the data accordingly.

In [32]:
print(f'The shape of the dataset after filtering: {df_educationR.loc[:, proportion1 <= 10.0].shape}')
df_education_filter = df_educationR.loc[:, proportion1 <= 10.0]
df_education_filter

The shape of the dataset after filtering: (250, 35)


CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

I can see that by filtering with a 10% threshold I have sliced the data down to 35 from 288 features. Considering that my economy dataset is the contains the primary target variable and is the main focus for this analysis, I am okay with the number of features dropped as these additional datasets primarily serve as additional factors to consider when creating the models.

In [33]:
# Filling in NaN values by Grouping by the CountryName column and transforming it in order to fillna by specific country mean values
df_education_fill = df_education_filter.groupby('CountryName').transform(lambda x: x.fillna(x.mean()))
print(f'The shape of the filled dataset: {df_education_fill.shape}')
df_education_fill # I will have to add in the CountryName and CountryCode columns to the combined dataset.

The shape of the filled dataset: (250, 33)


Year  Aquaculture production (metric tons)  CO2 emissions (kt)  \
0    1970.0                          1.900000e+01        9.376152e+04   
1    1971.0                          2.700000e+01        1.026357e+05   
2    1972.0                          5.000000e+01        1.143627e+05   
3    1973.0                          9.300000e+01        1.324630e+05   
4    1974.0                          1.580000e+02        1.434567e+05   
5    1975.0                          2.860000e+02        1.511647e+05   
6    1976.0                          4.330000e+02        1.551544e+05   
7    1977.0                          7.800000e+02        1.629615e+05   
8    1978.0                          1.132000e+03        1.769254e+05   
9    1979.0                          1.687000e+03        1.883225e+05   
10   1980.0                          3.737000e+03        1.870903e+05   
11   1981.0                          5.794000e+03        1.718063e+05   
12   1982.0                          7.586000e+03        1.721767e+05   
13   1983.0                          9.168000e+03        1.666321e+05   
14   1984.0                          1.070000e+04        1.688067e+05   
15   1985.0                          1.087300e+04        1.812488e+05   
16   1986.0                          1.099000e+04        1.988834e+05   
17   1987.0                          1.314000e+04        2.075302e+05   
18   1988.0                          1.555900e+04        2.093637e+05   
19   1989.0                          1.817000e+04        2.140245e+05   
20   1990.0                          2.049000e+04        2.088870e+05   
21   1991.0                          2.339000e+04        2.193306e+05   
22   1992.0                          2.982000e+04        2.207057e+05   
23   1993.0                          3.039000e+04        2.307386e+05   
24   1994.0                          3.091500e+04        2.421540e+05   
25   1995.0                          4.620200e+04        2.583475e+05   
26   1996.0                          7.769000e+04        2.847829e+05   
27   1997.0                          8.767600e+04        3.005473e+05   
28   1998.0                          1.039150e+05        3.122891e+05   
29   1999.0                          1.406570e+05        3.201731e+05   
30   2000.0                          1.724500e+05        3.279838e+05   
31   2001.0                          2.055680e+05        3.374337e+05   
32   2002.0                          2.476780e+05        3.322669e+05   
33   2003.0                          2.732680e+05        3.216216e+05   
34   2004.0                          2.696990e+05        3.378260e+05   
35   2005.0                          2.577840e+05        3.473089e+05   
36   2006.0                          2.716970e+05        3.476683e+05   
37   2007.0                          2.890480e+05        3.632127e+05   
38   2008.0                          3.315530e+05        3.876312e+05   
39   2009.0                          3.651270e+05        3.671474e+05   
40   2010.0                          4.117770e+05        4.197542e+05   
41   2011.0                          4.360840e+05        4.394129e+05   
42   2012.0                          4.808800e+05        4.700287e+05   
43   2013.0                          4.777520e+05        5.036771e+05   
44   2014.0                          5.642300e+05        5.335302e+05   
45   2015.0                          5.752300e+05        5.043885e+05   
46   2016.0                          5.812300e+05        4.622987e+05   
47   2017.0                          1.470762e+05        2.702110e+05   
48   2018.0                          1.470762e+05        2.702110e+05   
49   2019.0                          1.470762e+05        2.702110e+05   
50   1970.0                          1.294180e+06        7.716175e+05   
51   1971.0                          1.555198e+06        8.766330e+05   
52   1972.0                          1.708229e+06        9.315757e+05   
53   1973.0                          1.587984e+06        9.685427

The imputation worked and we can see again the CountryName and CountryCode columns were removed. I will add these using the insert dataframes created before. There is no need to reinitialize the df_insert1 and df_insert2 dataframes as the CountryName and CountryCode columns are exactly the same between the two datasets.

In [80]:
# In order to add these columns back into the dataframe I used insert to manually do so.
#df_education_fill.insert(0, 'CountryName', df_insert1) # The insert methods must be uncommented to add the two columns to the dataset
#df_education_fill.insert(1, 'CountryCode', df_insert2)
#df_education_fill = df_education_fill.drop('CountryName',axis=1) #this was used to make sure the position of the column was correct
df_education_fill

CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

In [35]:
# Check to see if imputation worked and no null values/duplicated rows
print(f'The shape of the cleaned dataset: {df_education_fill.shape}')
print(f'Check to see if there are duplicated data: {df_education_fill.duplicated().sum()/df_education_fill.shape[0]*100.0} percent')
df_education_fill.isna().sum()

The shape of the cleaned dataset: (250, 34)
Check to see if there are duplicated data: 0.0 percent


CountryCode                                                                          0
Year                                                                                 0
Aquaculture production (metric tons)                                                 0
CO2 emissions (kt)                                                                   0
CO2 emissions (metric tons per capita)                                               0
CO2 emissions from gaseous fuel consumption (% of total)                             0
CO2 emissions from gaseous fuel consumption (kt)                                     0
CO2 emissions from liquid fuel consumption (% of total)                              0
CO2 emissions from liquid fuel consumption (kt)                                      0
CO2 emissions from solid fuel consumption (% of total)                               0
CO2 emissions from solid fuel consumption (kt)                                       0
Forest rents (% of GDP)                    

With the second dataset cleaned and prepared for the EDA, now I will continue in the same steps for the rest of the 3 datasets.
### Public Dataset
Next, I will clean the public sector data that describes the different industries tied to the public sector and the different variables that affect growth and development in these countries.

In [36]:
# Taking a look at the original dataframe
print(f'The current shape of the dataset: {df_publicR.shape}')
df_publicR.head(10)

The current shape of the dataset: (250, 319)


CountryName CountryCode    Year  \
0      Brazil         BRA  1970.0   
1      Brazil         BRA  1971.0   
2      Brazil         BRA  1972.0   
3      Brazil         BRA  1973.0   
4      Brazil         BRA  1974.0   
5      Brazil         BRA  1975.0   
6      Brazil         BRA  1976.0   
7      Brazil         BRA  1977.0   
8      Brazil         BRA  1978.0   
9      Brazil         BRA  1979.0   

   Adequacy of social insurance programs (% of total welfare of beneficiary households)  \
0                                                NaN                                      
1                                                NaN                                      
2                                                NaN                                      
3                                                NaN                                      
4                                                NaN                                      
5                                                NaN                                      
6                                                NaN                                      
7                                                NaN                                      
8                                                NaN                                      
9                                                NaN                                      

   Adequacy of social protection and labor programs (% of total welfare of beneficiary households)  \
0                                                NaN                                                 
1                                                NaN                                                 
2                                                NaN                                                 
3                                                NaN                                                 
4                                                NaN                                                 
5                                                NaN                                                 
6                                                NaN                                                 
7                                                NaN                                                 
8                                                NaN                                                 
9                                                NaN                                                 

   Adequacy of social safety net programs (% of total welfare of beneficiary households)  \
0                                                NaN                                       
1                                                NaN                                       
2                                                NaN                                       
3                                                NaN                                       
4                                                NaN                                       
5                                                NaN                                       
6                                                NaN                                       
7                                                NaN                                       
8                                                NaN                                       
9                                                NaN                                       

   Adequacy of unemployment benefits and ALMP (% of total welfare of beneficiary households)  \
0                                                NaN                                           
1                                                NaN                                           
2                                                NaN                                           
3                                                NaN                    

In [37]:
float_columns = df_publicR.select_dtypes(['float64']).columns
print(f'The number of numeric type columns: {len(float_columns)}')
print(f'The shape of the public dataframe: {df_publicR.shape}')
df_publicR.dtypes # To show that the only datatypes that are string are CountryName and CountryCode

The number of numeric type columns: 317
The shape of the public dataframe: (250, 319)


CountryName                                                                                                                       object
CountryCode                                                                                                                       object
Year                                                                                                                             float64
Adequacy of social insurance programs (% of total welfare of beneficiary households)                                             float64
Adequacy of social protection and labor programs (% of total welfare of beneficiary households)                                  float64
Adequacy of social safety net programs (% of total welfare of beneficiary households)                                            float64
Adequacy of unemployment benefits and ALMP (% of total welfare of beneficiary households)                                        float64
Air transport, freight (million ton-km)  

In [38]:
# Checking to see if the length of the dataframe is the same as the shape method
len(df_publicR)

250

In [39]:
# Checking the number of null values by column
df_publicR.isna().sum()

CountryName                                                                                                                        0
CountryCode                                                                                                                        0
Year                                                                                                                               0
Adequacy of social insurance programs (% of total welfare of beneficiary households)                                             234
Adequacy of social protection and labor programs (% of total welfare of beneficiary households)                                  233
Adequacy of social safety net programs (% of total welfare of beneficiary households)                                            234
Adequacy of unemployment benefits and ALMP (% of total welfare of beneficiary households)                                        242
Air transport, freight (million ton-km)                              

In [40]:
# Getting the proportion of missing values by column, I used .mean as essentially I am taking the average * 100.0
proportion2 = df_publicR.isna().mean()*100
proportion2 #print(df_publicR.isna().sum()/len(df_publicR)*100)

CountryName                                                                                                                       0.0
CountryCode                                                                                                                       0.0
Year                                                                                                                              0.0
Adequacy of social insurance programs (% of total welfare of beneficiary households)                                             93.6
Adequacy of social protection and labor programs (% of total welfare of beneficiary households)                                  93.2
Adequacy of social safety net programs (% of total welfare of beneficiary households)                                            93.6
Adequacy of unemployment benefits and ALMP (% of total welfare of beneficiary households)                                        96.8
Air transport, freight (million ton-km)                       

I can see just by scrolling through the proportion of missing values within the dataset, that the public dataset has an extremely high proportion of missing values present within the available data. Considering this fact, I may adjust the threshold for this dataset in order to get more features back. For now, I will stick with 10% and see what the resulting dataset is.

In [41]:
print(f'The shape of the dataset after filtering: {df_publicR.loc[:, proportion2 <= 10.0].shape}')
df_public_filter = df_publicR.loc[:, proportion2 <= 10.0]
df_public_filter

The shape of the dataset after filtering: (250, 7)


CountryName CountryCode    Year  Fixed telephone subscriptions  \
0                Brazil         BRA  1970.0                      1250000.0   
1                Brazil         BRA  1971.0                            NaN   
2                Brazil         BRA  1972.0                            NaN   
3                Brazil         BRA  1973.0                            NaN   
4                Brazil         BRA  1974.0                            NaN   
5                Brazil         BRA  1975.0                      2201242.0   
6                Brazil         BRA  1976.0                      2510000.0   
7                Brazil         BRA  1977.0                      3060000.0   
8                Brazil         BRA  1978.0                      3720000.0   
9                Brazil         BRA  1979.0                      4290073.0   
10               Brazil         BRA  1980.0                      4950000.0   
11               Brazil         BRA  1981.0                      5330000.0   
12               Brazil         BRA  1982.0                      5822397.0   
13               Brazil         BRA  1983.0                      6300000.0   
14               Brazil         BRA  1984.0                      6700000.0   
15               Brazil         BRA  1985.0                      7201516.0   
16               Brazil         BRA  1986.0                      7451000.0   
17               Brazil         BRA  1987.0                      7810000.0   
18               Brazil         BRA  1988.0                      8270000.0   
19               Brazil         BRA  1989.0                      8790000.0   
20               Brazil         BRA  1990.0                      9409000.0   
21               Brazil         BRA  1991.0                     10075924.0   
22               Brazil         BRA  1992.0                     10841000.0   
23               Brazil         BRA  1993.0                     11303000.0   
24               Brazil         BRA  1994.0                     12269000.0   
25               Brazil         BRA  1995.0                     13263000.0   
26               Brazil         BRA  1996.0                     15105886.0   
27               Brazil         BRA  1997.0                     17038823.0   
28               Brazil         BRA  1998.0                     19986556.0   
29               Brazil         BRA  1999.0                     24985000.0   
30               Brazil         BRA  2000.0                     30926272.0   
31               Brazil         BRA  2001.0                     37430779.0   
32               Brazil         BRA  2002.0                     38810685.0   
33               Brazil         BRA  2003.0                     39205000.0   
34               Brazil         BRA  2004.0                     39578903.0   
35               Brazil         BRA  2005.0                     39852600.0   
36               Brazil         BRA  2006.0                     38800200.0   
37               Brazil         BRA  2007.0                     39399622.0   
38               Brazil         BRA  2008.0                     41235247.0   
39               Brazil         BRA  2009.0                     41496998.0   
40               Brazil         BRA  2010.0                     42141418.0   
41               Brazil         BRA  2011.0                     43025835.0   
42               Brazil         BRA  2012.0                     44305294.0   
43               Brazil         BRA  2013.0                     45038117.0   
44               Brazil         BRA  2014.0                     44128188.0   
45               Brazil         BRA  2015.0                     43677141.0   
46               Brazil         BRA  2016.0                     42003948.0   
47               Brazil         BRA  2017.0                     40375698.0   
48               Brazil         BRA  2018.0                     38311924.0   
49               Brazil         BRA  2019.0                     33700982.0   
50                China         CH

My guess was correct and through filtering with a 10% threshold, the resulting dataframe ended with 7 features for analysis from this dataframe. For the purpose of gaining a few more features that can be relevant to the target feature, I tested with a threshold of 15% too.

In [42]:
print(f'The shape of the dataset after filtering: {df_publicR.loc[:, proportion2 <= 15.0].shape}')
df_public_filter2 = df_publicR.loc[:, proportion2 <= 15.0]
df_public_filter2

The shape of the dataset after filtering: (250, 11)


CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

I can see that by increasing the threshold by 5% I was able to return more features that will be useful in understanding GDP growth, not just telephone related data. Although the data may become more skewed and biased if I impute on 15% instead of 10%, I decided that the features that outline the air transport industry and refugee population may provide interesting information for my analysis. I have effectively reduced the number of features from 319 to 11 by filtering. Next, I will impute the values using the same method as with economy and education datasets.

In [43]:
# Filling in NaN values by Grouping by the CountryName column and transforming it in order to fillna by specific country mean values
df_public_fill = df_public_filter2.groupby('CountryName').transform(lambda x: x.fillna(x.mean()))
print(f'The shape of the filled dataset: {df_public_fill.shape}')
df_public_fill # I will have to add in the CountryName and CountryCode columns to the combined dataset.

The shape of the filled dataset: (250, 9)


Year  Air transport, freight (million ton-km)  \
0    1970.0                               164.100006   
1    1971.0                               180.199997   
2    1972.0                               254.300003   
3    1973.0                               316.700012   
4    1974.0                               407.100006   
5    1975.0                               460.500000   
6    1976.0                               471.600006   
7    1977.0                               499.299988   
8    1978.0                               571.299988   
9    1979.0                               570.500000   
10   1980.0                               588.200012   
11   1981.0                               644.900024   
12   1982.0                               734.700012   
13   1983.0                               692.099976   
14   1984.0                               831.700012   
15   1985.0                               909.200012   
16   1986.0                              1014.400024   
17   1987.0                              1013.700012   
18   1988.0                               975.799988   
19   1989.0                              1147.900024   
20   1990.0                              1082.000000   
21   1991.0                              1005.299988   
22   1992.0                              1143.300049   
23   1993.0                              1284.300049   
24   1994.0                              1468.500000   
25   1995.0                              1581.900024   
26   1996.0                              1644.800049   
27   1997.0                              1789.900024   
28   1998.0                              1642.800049   
29   1999.0                              1462.900024   
30   2000.0                              1727.901000   
31   2001.0                              1467.445000   
32   2002.0                              1539.738000   
33   2003.0                              1478.370000   
34   2004.0                              1499.485000   
35   2005.0                              1530.675000   
36   2006.0                              1412.260000   
37   2007.0                              1477.828000   
38   2008.0                              1807.062000   
39   2009.0                              1782.300000   
40   2010.0                              1302.474648   
41   2011.0                              1294.495450   
42   2012.0                              1363.447091   
43   2013.0                              1637.382000   
44   2014.0                              1596.774000   
45   2015.0                              1493.939000   
46   2016.0                              1513.832873   
47   2017.0                              1736.549227   
48   2018.0                              1845.647756   
49   2019.0                              1144.112376   
50   1970.0                              6010.974761   
51   1971.0                              6010.974761   
52   1972.0                              6010.974761   
53   1973.0                              6010.974761   
54   1974.0                                29.200001   
55   1975.0                                46.200001   
56   1976.0                                49.000000   
57   1977.0                                60.000000   
58   1978.0                                86.000000   
59   1979.0                               123.000000   
60   1980.0                               120.900002   
61   1981.0                               155.399994   
62   1982.0                               184.199997   
63   1983.0                               216.000000   
64   1984.0                               302.000000   
65   1985.0                               403.000000   
66   1986.0                               467.500000   
67   1987.0                               647.500000   
68   1988.0                               731.799988   
69   1989.0                               683.099976   
70   1990.0                    

In [81]:
# In order to add these columns back into the dataframe I used insert to manually do so.
#df_public_fill.insert(0, 'CountryName', df_insert1) # The insert methods must be uncommented to add the two columns to the dataset
#df_public_fill.insert(1, 'CountryCode', df_insert2)
#df_public_fill = df_public_fill.drop('CountryName',axis=1) # this was used to make sure the position of the column was correct
df_public_fill

CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

In [45]:
# Check to see if imputation worked and no null values/duplicated rows
print(f'The shape of the cleaned dataset: {df_public_fill.shape}')
print(f'Check to see if there are duplicated data: {df_public_fill.duplicated().sum()/df_public_fill.shape[0]*100.0} percent')
df_public_fill.isna().sum()

The shape of the cleaned dataset: (250, 10)
Check to see if there are duplicated data: 0.0 percent


CountryCode                                               0
Year                                                      0
Air transport, freight (million ton-km)                   0
Air transport, passengers carried                         0
Air transport, registered carrier departures worldwide    0
Fixed telephone subscriptions                             0
Fixed telephone subscriptions (per 100 people)            0
Mobile cellular subscriptions                             0
Mobile cellular subscriptions (per 100 people)            0
Refugee population by country or territory of origin      0
dtype: int64

With the third dataset cleaned and prepared for the EDA, now I will continue in the same steps for the rest of the 2 datasets.
### Private Dataset
Next, I will clean the private sector data that provides insight on different industries that are not listed publically and how they contribute to the BRICS analysis.

In [46]:
# Taking a look at the original dataframe
print(f'The current shape of the dataset: {df_privateR.shape}')
df_privateR.head(10)

The current shape of the dataset: (230, 171)


CountryName CountryCode    Year  \
0      Brazil         BRA  1970.0   
1      Brazil         BRA  1971.0   
2      Brazil         BRA  1972.0   
3      Brazil         BRA  1973.0   
4      Brazil         BRA  1974.0   
5      Brazil         BRA  1975.0   
6      Brazil         BRA  1976.0   
7      Brazil         BRA  1977.0   
8      Brazil         BRA  1978.0   
9      Brazil         BRA  1979.0   

   Agricultural raw materials exports (% of merchandise exports)  \
0                                          11.895098               
1                                          10.494023               
2                                           9.322425               
3                                           8.521143               
4                                           5.991149               
5                                           3.891622               
6                                           2.273232               
7                                           2.353515               
8                                           2.918907               
9                                           3.442275               

   Agricultural raw materials imports (% of merchandise imports)  \
0                                           1.851044               
1                                           2.178320               
2                                           1.971959               
3                                           2.073260               
4                                           2.014877               
5                                           1.497433               
6                                           1.418146               
7                                           1.458700               
8                                           1.447775               
9                                           1.351869               

   Average number of visits or required meetings with tax officials (for affected firms)  \
0                                                NaN                                       
1                                                NaN                                       
2                                                NaN                                       
3                                                NaN                                       
4                                                NaN                                       
5                                                NaN                                       
6                                                NaN                                       
7                                                NaN                                       
8                                                NaN                                       
9                                                NaN                                       

   Average time to clear exports through customs (days)  \
0                                                NaN      
1                                                NaN      
2                                                NaN      
3                                                NaN      
4                                                NaN      
5                                                NaN      
6                                                NaN      
7                                                NaN      
8                                                NaN      
9                                                NaN      

   Binding coverage, all products (%)  \
0                                 NaN   
1                                 NaN   
2                                 NaN   
3                                 NaN   
4                                 NaN   
5                                 NaN   
6                                 NaN   
7                                 NaN   
8                                 NaN   
9                      

Immediately, one problem that I noticed about this dataset is that the shape does not align with the other datasetes as the number of rows is 230 not 250. I will need to first find where the missing rows are and impute the values even if they are NaN values in order to continue with the cleaning.

In [47]:
df_privateR

CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

Looking for the 20 rows not present in the data, I found Russia 1970-1989 (20 rows) missing from the dataframe. I will need to clean it once the combined dataframe is created as I should be able to add the rows using the concat method. I will perform one last cleaning on the combined dataset at the end.

In [137]:
# This was the idea I had for slicing in the rows where the missing rows were present, this however seemed inefficient to me.
#row1 = ["Russian Federation"]
#insert_row1 = pd.DataFrame(index = ["150"])
#insert_index1 = len(df_privateR.index)-80
#df_privateR2 = df_privateR.iloc[:insert_index1,].append([insert_row1, df_privateR.iloc[insert_index1:,]])
#df_privateR2

In [48]:
# Checking the number of columns that are type float64 and the size of the dataset, there should be 333 features that are type float64.
float_columns = df_privateR.select_dtypes(['float64']).columns
print(f'The number of numeric type columns: {len(float_columns)}')
print(f'The shape of the economy dataframe: {df_privateR.shape}')
df_privateR.dtypes # To show that the only datatypes that are string are CountryName and CountryCode

The number of numeric type columns: 169
The shape of the economy dataframe: (230, 171)


CountryName                                                                                                                         object
CountryCode                                                                                                                         object
Year                                                                                                                               float64
Agricultural raw materials exports (% of merchandise exports)                                                                      float64
Agricultural raw materials imports (% of merchandise imports)                                                                      float64
Average number of visits or required meetings with tax officials (for affected firms)                                              float64
Average time to clear exports through customs (days)                                                                               float64
Binding coverage, all produ

I can see that the features that are numeric and non-numeric are the same for the private dataframe, which is a good sign. Now, I will check for null values and the proportion of missing values they are.

In [49]:
# Checking the number of null values by column
df_privateR.isna().sum()

CountryName                                                                                                                          0
CountryCode                                                                                                                          0
Year                                                                                                                                 0
Agricultural raw materials exports (% of merchandise exports)                                                                       32
Agricultural raw materials imports (% of merchandise imports)                                                                       32
Average number of visits or required meetings with tax officials (for affected firms)                                              223
Average time to clear exports through customs (days)                                                                               220
Binding coverage, all products (%)                     

In [50]:
# Getting the proportion of missing values by column, I used .mean as essentially I am taking the average * 100.0
proportion3 = df_privateR.isna().mean()*100
proportion3 #print(df_privateR.isna().sum()/len(df_privateR)*100)

CountryName                                                                                                                         0.000000
CountryCode                                                                                                                         0.000000
Year                                                                                                                                0.000000
Agricultural raw materials exports (% of merchandise exports)                                                                      13.913043
Agricultural raw materials imports (% of merchandise imports)                                                                      13.913043
Average number of visits or required meetings with tax officials (for affected firms)                                              96.956522
Average time to clear exports through customs (days)                                                                               95.652174
Binding cover

From the results above, I can see that there are many features with a high proportion of null values, with a decent amount with a low proportion. For this particular dataframe, I will set the threshold to 10% as it seems there will be enough features with relevant data for the analysis.

In [51]:
print(f'The shape of the dataset after filtering: {df_privateR.loc[:, proportion3 <= 10.0].shape}')
df_private_filter = df_privateR.loc[:, proportion3 <= 10.0]
df_private_filter

The shape of the dataset after filtering: (230, 18)


CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

By using the filtering technique, I am now left with 18 features from 171 originally. Next, I will impute the values that have less than or equal to 10% of the missing values present in the dataframe.

In [52]:
# Filling in NaN values by Grouping by the CountryName column and transforming it in order to fillna by specific country mean values
df_private_fill = df_private_filter.groupby('CountryName').transform(lambda x: x.fillna(x.mean()))
print(f'The shape of the filled dataset: {df_private_fill.shape}')
df_private_fill # I will have to add in the CountryName and CountryCode columns to the combined dataset.

The shape of the filled dataset: (230, 16)


Year  Merchandise exports (current US$)  \
0    1970.0                       2.739000e+09   
1    1971.0                       2.904000e+09   
2    1972.0                       3.991000e+09   
3    1973.0                       6.199000e+09   
4    1974.0                       7.951000e+09   
5    1975.0                       8.670000e+09   
6    1976.0                       1.012800e+10   
7    1977.0                       1.212000e+10   
8    1978.0                       1.265900e+10   
9    1979.0                       1.524400e+10   
10   1980.0                       2.013200e+10   
11   1981.0                       2.329300e+10   
12   1982.0                       2.017500e+10   
13   1983.0                       2.189900e+10   
14   1984.0                       2.700500e+10   
15   1985.0                       2.563900e+10   
16   1986.0                       2.234900e+10   
17   1987.0                       2.622400e+10   
18   1988.0                       3.349400e+10   
19   1989.0                       3.438300e+10   
20   1990.0                       3.141400e+10   
21   1991.0                       3.162000e+10   
22   1992.0                       3.579300e+10   
23   1993.0                       3.855500e+10   
24   1994.0                       4.354500e+10   
25   1995.0                       4.650600e+10   
26   1996.0                       4.774700e+10   
27   1997.0                       5.299400e+10   
28   1998.0                       5.114000e+10   
29   1999.0                       4.801300e+10   
30   2000.0                       5.511900e+10   
31   2001.0                       5.828700e+10   
32   2002.0                       6.043900e+10   
33   2003.0                       7.320300e+10   
34   2004.0                       9.667800e+10   
35   2005.0                       1.185290e+11   
36   2006.0                       1.378070e+11   
37   2007.0                       1.606490e+11   
38   2008.0                       1.979420e+11   
39   2009.0                       1.529950e+11   
40   2010.0                       2.019150e+11   
41   2011.0                       2.560400e+11   
42   2012.0                       2.425780e+11   
43   2013.0                       2.420340e+11   
44   2014.0                       2.251010e+11   
45   2015.0                       1.911340e+11   
46   2016.0                       1.852320e+11   
47   2017.0                       2.177390e+11   
48   2018.0                       2.392640e+11   
49   2019.0                       2.253830e+11   
50   1970.0                       2.307000e+09   
51   1971.0                       2.783000e+09   
52   1972.0                       3.693000e+09   
53   1973.0                       5.876000e+09   
54   1974.0                       7.108000e+09   
55   1975.0                       7.689000e+09   
56   1976.0                       6.943000e+09   
57   1977.0                       7.520000e+09   
58   1978.0                       9.955000e+09   
59   1979.0                       1.361400e+10   
60   1980.0                       1.809900e+10   
61   1981.0                       2.200700e+10   
62   1982.0                       2.232100e+10   
63   1983.0                       2.222600e+10   
64   1984.0                       2.613900e+10   
65   1985.0                       2.735000e+10   
66   1986.0                       3.094200e+10   
67   1987.0                       3.943700e+10   
68   1988.0                       4.751600e+10   
69   1989.0                       5.253800e+10   
70   1990.0                       6.209100e+10   
71   1991.0                       7.191000e+10   
72   1992.0                       8.494000e+10   
73   1993.0                       9.174400e+10   
74   1994.0                       1.210060e+11   
75   1995.0                       1.487800e+11   
76   1996.0                       1.510480e+11   
77   1997.0                       1.827920e+11   
78   1998.0                       1.837120e+11   
79   19

Now that the imputation has been completed, I will add the CountryName and CountryCode columns in order to combine the dataset later.

In [82]:
# In order to add these columns back into the dataframe I used insert to manually do so.
#df_private_fill.insert(0, 'CountryName', df_insert1) # The insert methods must be uncommented to add the two columns to the dataset
#df_private_fill.insert(1, 'CountryCode', df_insert2)
#df_private_fill = df_private_fill.drop('CountryName',axis=1) # this was used to make sure the position of the column was correct
df_private_fill

CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

In [55]:
# Check to see if imputation worked and no null values/duplicated rows
print(f'The shape of the cleaned dataset: {df_private_fill.shape}')
print(f'Check to see if there are duplicated data: {df_private_fill.duplicated().sum()/df_private_fill.shape[0]*100.0} percent')
df_private_fill.isna().sum()

The shape of the cleaned dataset: (230, 17)
Check to see if there are duplicated data: 0.0 percent


CountryCode                                                                                                                  0
Year                                                                                                                         0
Merchandise exports (current US$)                                                                                            0
Merchandise exports by the reporting economy (current US$)                                                                   0
Merchandise exports by the reporting economy, residual (% of total merchandise exports)                                      0
Merchandise exports to economies in the Arab World (% of total merchandise exports)                                          0
Merchandise exports to high-income economies (% of total merchandise exports)                                                0
Merchandise exports to low- and middle-income economies in East Asia & Pacific (% of total merchandise exports)

With the fourth dataset cleaned and prepared for the EDA, now I will continue in the same steps for the last dataset.
### Health Dataset
Finally, I will clean the health data that provides demographic and general lifestyle insight on different health related aspects in the BRICS countries.

In [56]:
# Taking a look at the original dataframe
print(f'The current shape of the dataset: {df_healthR.shape}')
df_healthR.head(10)

The current shape of the dataset: (250, 266)


CountryName CountryCode    Year  \
0      Brazil         BRA  1970.0   
1      Brazil         BRA  1971.0   
2      Brazil         BRA  1972.0   
3      Brazil         BRA  1973.0   
4      Brazil         BRA  1974.0   
5      Brazil         BRA  1975.0   
6      Brazil         BRA  1976.0   
7      Brazil         BRA  1977.0   
8      Brazil         BRA  1978.0   
9      Brazil         BRA  1979.0   

   ARI treatment (% of children under 5 taken to a health provider)  \
0                                                NaN                  
1                                                NaN                  
2                                                NaN                  
3                                                NaN                  
4                                                NaN                  
5                                                NaN                  
6                                                NaN                  
7                                                NaN                  
8                                                NaN                  
9                                                NaN                  

   Adolescent fertility rate (births per 1,000 women ages 15-19)  \
0                                            77.1184               
1                                            75.4532               
2                                            73.7880               
3                                            73.8080               
4                                            73.8280               
5                                            73.8480               
6                                            73.8680               
7                                            73.8880               
8                                            75.0802               
9                                            76.2724               

   Adults (ages 15+) and children (ages 0-14) newly infected with HIV  \
0                                                NaN                    
1                                                NaN                    
2                                                NaN                    
3                                                NaN                    
4                                                NaN                    
5                                                NaN                    
6                                                NaN                    
7                                                NaN                    
8                                                NaN                    
9                                                NaN                    

   Adults (ages 15-49) newly infected with HIV  \
0                                          NaN   
1                                          NaN   
2                                          NaN   
3                                          NaN   
4                                          NaN   
5                                          NaN   
6                                          NaN   
7                                          NaN   
8                                          NaN   
9                                          NaN   

   Age dependency ratio (% of working-age population)  \
0                                          83.980449    
1                                          82.948217    
2                                          81.878391    
3                                          80.746489    
4                                          79.514392    
5                                          78.196756    
6                                          77.037268    
7                                          75.877456    
8                                          74.720059    
9                                          73.578631    

   Age dependency ratio, old (% of working-age population)  \
0                 

Looking at this dataframe, I can see that there will be a large number of features that will be dropped as many of the columns show many Nan values. Further, the shape of the dataframe fits with the other dataframes, making it useful in the concat process. Next, I will check the datatypes for each feature.

In [57]:
# Checking the number of columns that are type float64 and the size of the dataset
float_columns = df_healthR.select_dtypes(['float64']).columns
print(f'The number of numeric type columns: {len(float_columns)}')
print(f'The shape of the health dataframe: {df_healthR.shape}')
df_healthR.dtypes # To show that the only datatypes that are string are CountryName and CountryCode

The number of numeric type columns: 264
The shape of the health dataframe: (250, 266)


CountryName                                                                                                                         object
CountryCode                                                                                                                         object
Year                                                                                                                               float64
ARI treatment (% of children under 5 taken to a health provider)                                                                   float64
Adolescent fertility rate (births per 1,000 women ages 15-19)                                                                      float64
Adults (ages 15+) and children (ages 0-14) newly infected with HIV                                                                 float64
Adults (ages 15-49) newly infected with HIV                                                                                        float64
Age dependency ratio (% of 

The framework above fits inline with the other dataframes as the only two columns that are not numeric are CountryName and CountryCode. Next, I will check for null values and find the proportion missing for each feature in the dataframe.

In [58]:
# Checking to see if the length of the dataframe is the same as the shape method
len(df_healthR)

250

In [59]:
# Checking the number of null values by column
df_healthR.isna().sum()

CountryName                                                                                                                          0
CountryCode                                                                                                                          0
Year                                                                                                                                 0
ARI treatment (% of children under 5 taken to a health provider)                                                                   239
Adolescent fertility rate (births per 1,000 women ages 15-19)                                                                        5
Adults (ages 15+) and children (ages 0-14) newly infected with HIV                                                                 190
Adults (ages 15-49) newly infected with HIV                                                                                        220
Age dependency ratio (% of working-age population)     

In [61]:
# Getting the proportion of missing values by column, I used .mean as essentially I am taking the average * 100.0
proportion4 = df_healthR.isna().mean()*100
proportion4 #print(df_healthR.isna().sum()/len(df_healthR)*100)

CountryName                                                                                                                         0.0
CountryCode                                                                                                                         0.0
Year                                                                                                                                0.0
ARI treatment (% of children under 5 taken to a health provider)                                                                   95.6
Adolescent fertility rate (births per 1,000 women ages 15-19)                                                                       2.0
Adults (ages 15+) and children (ages 0-14) newly infected with HIV                                                                 76.0
Adults (ages 15-49) newly infected with HIV                                                                                        88.0
Age dependency ratio (% of working-age populatio

Looking at the proportion of missing values for each feature in the dataframe, I can seee that some features contain no null values, while other have a high proportion. I will set the threshold fo 10% instead of 15% as this dataframe seems to have more features with a low proportion of missing values. I will now slice the data according to the filter technique.

In [62]:
print(f'The shape of the dataset after filtering: {df_healthR.loc[:, proportion4 <= 10.0].shape}')
df_health_filter = df_healthR.loc[:, proportion4 <= 10.0]
df_health_filter

The shape of the dataset after filtering: (250, 83)


CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

By using the filtering technique, I can see that the number of features has been sliced from 266 to 83.

In [63]:
# Filling in NaN values by Grouping by the CountryName column and transforming it in order to fillna by specific country mean values
df_health_fill = df_health_filter.groupby('CountryName').transform(lambda x: x.fillna(x.mean()))
print(f'The shape of the filled dataset: {df_health_fill.shape}')
df_health_fill # I will have to add in the CountryName and CountryCode columns to the combined dataset.

The shape of the filled dataset: (250, 81)


Year  Adolescent fertility rate (births per 1,000 women ages 15-19)  \
0    1970.0                                          77.118400               
1    1971.0                                          75.453200               
2    1972.0                                          73.788000               
3    1973.0                                          73.808000               
4    1974.0                                          73.828000               
5    1975.0                                          73.848000               
6    1976.0                                          73.868000               
7    1977.0                                          73.888000               
8    1978.0                                          75.080200               
9    1979.0                                          76.272400               
10   1980.0                                          77.464600               
11   1981.0                                          78.656800               
12   1982.0                                          79.849000               
13   1983.0                                          80.231400               
14   1984.0                                          80.613800               
15   1985.0                                          80.996200               
16   1986.0                                          81.378600               
17   1987.0                                          81.761000               
18   1988.0                                          82.154200               
19   1989.0                                          82.547400               
20   1990.0                                          82.940600               
21   1991.0                                          83.333800               
22   1992.0                                          83.727000               
23   1993.0                                          83.834000               
24   1994.0                                          83.941000               
25   1995.0                                          84.048000               
26   1996.0                                          84.155000               
27   1997.0                                          84.262000               
28   1998.0                                          83.578000               
29   1999.0                                          82.894000               
30   2000.0                                          82.210000               
31   2001.0                                          81.526000               
32   2002.0                                          80.842000               
33   2003.0                                          78.904000               
34   2004.0                                          76.966000               
35   2005.0                                          75.028000               
36   2006.0                                          73.090000               
37   2007.0                                          71.152000               
38   2008.0                                          69.732200               
39   2009.0                                          68.312400               
40   2010.0                                          66.892600               
41   2011.0                                          65.472800               
42   2012.0                                          64.053000               
43   2013.0                                          63.064600               
44   2014.0                                          62.076200               
45   2015.0                                          61.087800               
46   2016.0                                          60.099400               
47   2017.0                                          59.111000               
48   2018.0                                          57.885800               
49   2019.0                                          75.649478               
50   1970.0                  

With the imputation process finished, now I have to add the CountryName and CountyCode columns that were removed in the previous process. I will add the dataframes made in the first dataset as the columns match accordingly.

In [83]:
# In order to add these columns back into the dataframe I used insert to manually do so.
#df_health_fill.insert(0, 'CountryName', df_insert1) # The insert methods must be uncommented to add the two columns to the dataset
#df_health_fill.insert(1, 'CountryCode', df_insert2)
#df_health_fill = df_health_fill.drop('CountryName',axis=1) # this was used to make sure the position of the column was correct
df_health_fill

CountryName CountryCode    Year  \
0                Brazil         BRA  1970.0   
1                Brazil         BRA  1971.0   
2                Brazil         BRA  1972.0   
3                Brazil         BRA  1973.0   
4                Brazil         BRA  1974.0   
5                Brazil         BRA  1975.0   
6                Brazil         BRA  1976.0   
7                Brazil         BRA  1977.0   
8                Brazil         BRA  1978.0   
9                Brazil         BRA  1979.0   
10               Brazil         BRA  1980.0   
11               Brazil         BRA  1981.0   
12               Brazil         BRA  1982.0   
13               Brazil         BRA  1983.0   
14               Brazil         BRA  1984.0   
15               Brazil         BRA  1985.0   
16               Brazil         BRA  1986.0   
17               Brazil         BRA  1987.0   
18               Brazil         BRA  1988.0   
19               Brazil         BRA  1989.0   
20               Brazil         BRA  1990.0   
21               Brazil         BRA  1991.0   
22               Brazil         BRA  1992.0   
23               Brazil         BRA  1993.0   
24               Brazil         BRA  1994.0   
25               Brazil         BRA  1995.0   
26               Brazil         BRA  1996.0   
27               Brazil         BRA  1997.0   
28               Brazil         BRA  1998.0   
29               Brazil         BRA  1999.0   
30               Brazil         BRA  2000.0   
31               Brazil         BRA  2001.0   
32               Brazil         BRA  2002.0   
33               Brazil         BRA  2003.0   
34               Brazil         BRA  2004.0   
35               Brazil         BRA  2005.0   
36               Brazil         BRA  2006.0   
37               Brazil         BRA  2007.0   
38               Brazil         BRA  2008.0   
39               Brazil         BRA  2009.0   
40               Brazil         BRA  2010.0   
41               Brazil         BRA  2011.0   
42               Brazil         BRA  2012.0   
43               Brazil         BRA  2013.0   
44               Brazil         BRA  2014.0   
45               Brazil         BRA  2015.0   
46               Brazil         BRA  2016.0   
47               Brazil         BRA  2017.0   
48               Brazil         BRA  2018.0   
49               Brazil         BRA  2019.0   
50                China         CHN  1970.0   
51                China         CHN  1971.0   
52                China         CHN  1972.0   
53                China         CHN  1973.0   
54                China         CHN  1974.0   
55                China         CHN  1975.0   
56                China         CHN  1976.0   
57                China         CHN  1977.0   
58                China         CHN  1978.0   
59                China         CHN  1979.0   
60                China         CHN  1980.0   
61                China         CHN  1981.0   
62                China         CHN  1982.0   
63                China         CHN  1983.0   
64                China         CHN  1984.0   
65                China         CHN  1985.0   
66                China         CHN  1986.0   
67                China         CHN  1987.0   
68                China         CHN  1988.0   
69                China         CHN  1989.0   
70                China         CHN  1990.0   
71                China         CHN  1991.0   
72                China         CHN  1992.0   
73                China         CHN  1993.0   
74                China         CHN  1994.0   
75                China         CHN  1995.0   
76                China         CHN  1996.0   
77                China         CHN  1997.0   
78                China         CHN  1998.0   
79                China         CHN  1999.0   
80                China         CHN  2000.0   
81                China         CHN  2001.0   
82                China         CHN  2002.0   
83                China         CHN  2003.0   
84               

In [65]:
# Check to see if imputation worked and no null values/duplicated rows
print(f'The shape of the cleaned dataset: {df_health_fill.shape}')
print(f'Check to see if there are duplicated data: {df_health_fill.duplicated().sum()/df_health_fill.shape[0]*100.0} percent')
df_health_fill.isna().sum()

The shape of the cleaned dataset: (250, 82)
Check to see if there are duplicated data: 0.0 percent


CountryCode                                                      0
Year                                                             0
Adolescent fertility rate (births per 1,000 women ages 15-19)    0
Age dependency ratio (% of working-age population)               0
Age dependency ratio, old (% of working-age population)          0
Age dependency ratio, young (% of working-age population)        0
Birth rate, crude (per 1,000 people)                             0
Death rate, crude (per 1,000 people)                             0
Fertility rate, total (births per woman)                         0
Life expectancy at birth, female (years)                         0
Life expectancy at birth, male (years)                           0
Life expectancy at birth, total (years)                          0
Mortality rate, adult, female (per 1,000 female adults)          0
Mortality rate, adult, male (per 1,000 male adults)              0
Mortality rate, infant (per 1,000 live births)                

Now that all dataframes have been cleaned and filled with the imputation method, I can proceed to create a combined dataframe that contains all features from the 5 different datasets.

### Creating a Master Dataset for Analysis
With all of the 5 datasets cleaned, now I will combined all of them on the CountryName, CountryCode, and Year columns as all datasets have a similar column for merging.

In [84]:
# All datasets
pdList = [df_economy_fill, df_education_fill, df_public_fill, df_private_fill, df_health_fill]
df_master = pd.concat(pdList, axis=1)
df_master.head(20) # The combined 5 dataframes, may need to readjust for the missing 20 rows seen in the df_private_fill dataframe.

CountryName CountryCode    Year  \
0       Brazil         BRA  1970.0   
1       Brazil         BRA  1971.0   
2       Brazil         BRA  1972.0   
3       Brazil         BRA  1973.0   
4       Brazil         BRA  1974.0   
5       Brazil         BRA  1975.0   
6       Brazil         BRA  1976.0   
7       Brazil         BRA  1977.0   
8       Brazil         BRA  1978.0   
9       Brazil         BRA  1979.0   
10      Brazil         BRA  1980.0   
11      Brazil         BRA  1981.0   
12      Brazil         BRA  1982.0   
13      Brazil         BRA  1983.0   
14      Brazil         BRA  1984.0   
15      Brazil         BRA  1985.0   
16      Brazil         BRA  1986.0   
17      Brazil         BRA  1987.0   
18      Brazil         BRA  1988.0   
19      Brazil         BRA  1989.0   

    Adjusted savings: carbon dioxide damage (% of GNI)  \
0                                            0.372691    
1                                            0.378426    
2                                            0.379821    
3                                            0.354143    
4                                            0.323506    
5                                            0.328014    
6                                            0.296894    
7                                            0.296063    
8                                            0.313108    
9                                            0.332934    
10                                           0.357798    
11                                           0.333266    
12                                           0.345343    
13                                           0.499338    
14                                           0.524224    
15                                           0.558641    
16                                           0.530679    
17                                           0.529146    
18                                           0.507813    
19                                           0.392948    

    Adjusted savings: carbon dioxide damage (current US$)  \
0                                        1.555186e+08       
1                                        1.842334e+08       
2                                        2.205824e+08       
3                                        2.775798e+08       
4                                        3.374990e+08       
5                                        4.002313e+08       
6                                        4.464043e+08       
7                                        5.129387e+08       
8                                        6.139444e+08       
9                                        7.289420e+08       
10                                       8.132752e+08       
11                                       8.420280e+08       
12                                       9.228570e+08       
13                                       9.559647e+08       
14                                       1.033480e+09       
15                                       1.179088e+09       
16                                       1.359460e+09       
17                                       1.497248e+09       
18                                       1.610669e+09       
19                                       1.762407e+09       

    Adjusted savings: consumption of fixed capital (% of GNI)  \
0                                            9.017633           
1                                            9.085182           
2                                            9.310639           
3                                            9.691598           
4                                            9.837892           
5                                           10.353115           
6                                           10.562495           
7                                           10.467414           
8                                           10.731192           
9                                           10.966655

In [90]:
# Creating a CSV file for the cleaning section, remove the repeated columns manually using Excel (CountryName, CountryCode, Year) as they were manually added
df_master.to_csv(r'C:\Users\Jim\Desktop\df_master.csv')

In [109]:
# Reading in the partially cleaned combined dataset, should have 12 less features as (CountryName, CountryCode, Year) * 4.
df_master_fix = pd.read_csv('Data/df_master_fix.csv', index_col = 0)
df_master_fix.head(20)

CountryName CountryCode  Year  \
0       Brazil         BRA  1970   
1       Brazil         BRA  1971   
2       Brazil         BRA  1972   
3       Brazil         BRA  1973   
4       Brazil         BRA  1974   
5       Brazil         BRA  1975   
6       Brazil         BRA  1976   
7       Brazil         BRA  1977   
8       Brazil         BRA  1978   
9       Brazil         BRA  1979   
10      Brazil         BRA  1980   
11      Brazil         BRA  1981   
12      Brazil         BRA  1982   
13      Brazil         BRA  1983   
14      Brazil         BRA  1984   
15      Brazil         BRA  1985   
16      Brazil         BRA  1986   
17      Brazil         BRA  1987   
18      Brazil         BRA  1988   
19      Brazil         BRA  1989   

    Adjusted savings: carbon dioxide damage (% of GNI)  \
0                                            0.372691    
1                                            0.378426    
2                                            0.379821    
3                                            0.354143    
4                                            0.323506    
5                                            0.328014    
6                                            0.296894    
7                                            0.296063    
8                                            0.313108    
9                                            0.332933    
10                                           0.357798    
11                                           0.333266    
12                                           0.345343    
13                                           0.499338    
14                                           0.524224    
15                                           0.558641    
16                                           0.530679    
17                                           0.529146    
18                                           0.507813    
19                                           0.392948    

    Adjusted savings: carbon dioxide damage (current US$)  \
0                                        1.555186e+08       
1                                        1.842334e+08       
2                                        2.205824e+08       
3                                        2.775798e+08       
4                                        3.374990e+08       
5                                        4.002313e+08       
6                                        4.464043e+08       
7                                        5.129387e+08       
8                                        6.139444e+08       
9                                        7.289420e+08       
10                                       8.132752e+08       
11                                       8.420280e+08       
12                                       9.228570e+08       
13                                       9.559647e+08       
14                                       1.033480e+09       
15                                       1.179088e+09       
16                                       1.359460e+09       
17                                       1.497248e+09       
18                                       1.610669e+09       
19                                       1.762407e+09       

    Adjusted savings: consumption of fixed capital (% of GNI)  \
0                                            9.017633           
1                                            9.085182           
2                                            9.310639           
3                                            9.691598           
4                                            9.837892           
5                                           10.353115           
6                                           10.562495           
7                                           10.467414           
8                                           10.731192           
9                                           10.966655           
10                            

In [110]:
# Check to see where the 20 missing rows are from the df_privateR Dataset
df_master_fix.isna().sum()

CountryName                                                                                                                   0
CountryCode                                                                                                                   0
Year                                                                                                                          0
Adjusted savings: carbon dioxide damage (% of GNI)                                                                            0
Adjusted savings: carbon dioxide damage (current US$)                                                                         0
Adjusted savings: consumption of fixed capital (% of GNI)                                                                     0
Adjusted savings: consumption of fixed capital (current US$)                                                                  0
Adjusted savings: education expenditure (% of GNI)                                                      

As we can see, the only present NaN values present in the combined dataframe are the rows identified in the cleaning of df_privateR. I will now impute the missing values as they accounted for less than 10% of the missing data.

In [111]:
# Getting the proportion of missing values by column, I used .mean as essentially I am taking the average * 100.0
proportion5 = df_master_fix.isna().mean()*100
proportion5 #print(df_master_fix.isna().sum()/len(df_master_fix)*100)

CountryName                                                                                                                  0.0
CountryCode                                                                                                                  0.0
Year                                                                                                                         0.0
Adjusted savings: carbon dioxide damage (% of GNI)                                                                           0.0
Adjusted savings: carbon dioxide damage (current US$)                                                                        0.0
Adjusted savings: consumption of fixed capital (% of GNI)                                                                    0.0
Adjusted savings: consumption of fixed capital (current US$)                                                                 0.0
Adjusted savings: education expenditure (% of GNI)                                               

In [112]:
# Enable the 10% threshold on the dataset
print(f'The shape of the dataset after filtering: {df_master_fix.loc[:, proportion5 <= 10.0].shape}')
df_master_filter = df_master_fix.loc[:, proportion5 <= 10.0]
df_master_filter

The shape of the dataset after filtering: (250, 211)


CountryName CountryCode  Year  \
0                Brazil         BRA  1970   
1                Brazil         BRA  1971   
2                Brazil         BRA  1972   
3                Brazil         BRA  1973   
4                Brazil         BRA  1974   
5                Brazil         BRA  1975   
6                Brazil         BRA  1976   
7                Brazil         BRA  1977   
8                Brazil         BRA  1978   
9                Brazil         BRA  1979   
10               Brazil         BRA  1980   
11               Brazil         BRA  1981   
12               Brazil         BRA  1982   
13               Brazil         BRA  1983   
14               Brazil         BRA  1984   
15               Brazil         BRA  1985   
16               Brazil         BRA  1986   
17               Brazil         BRA  1987   
18               Brazil         BRA  1988   
19               Brazil         BRA  1989   
20               Brazil         BRA  1990   
21               Brazil         BRA  1991   
22               Brazil         BRA  1992   
23               Brazil         BRA  1993   
24               Brazil         BRA  1994   
25               Brazil         BRA  1995   
26               Brazil         BRA  1996   
27               Brazil         BRA  1997   
28               Brazil         BRA  1998   
29               Brazil         BRA  1999   
30               Brazil         BRA  2000   
31               Brazil         BRA  2001   
32               Brazil         BRA  2002   
33               Brazil         BRA  2003   
34               Brazil         BRA  2004   
35               Brazil         BRA  2005   
36               Brazil         BRA  2006   
37               Brazil         BRA  2007   
38               Brazil         BRA  2008   
39               Brazil         BRA  2009   
40               Brazil         BRA  2010   
41               Brazil         BRA  2011   
42               Brazil         BRA  2012   
43               Brazil         BRA  2013   
44               Brazil         BRA  2014   
45               Brazil         BRA  2015   
46               Brazil         BRA  2016   
47               Brazil         BRA  2017   
48               Brazil         BRA  2018   
49               Brazil         BRA  2019   
50                China         CHN  1970   
51                China         CHN  1971   
52                China         CHN  1972   
53                China         CHN  1973   
54                China         CHN  1974   
55                China         CHN  1975   
56                China         CHN  1976   
57                China         CHN  1977   
58                China         CHN  1978   
59                China         CHN  1979   
60                China         CHN  1980   
61                China         CHN  1981   
62                China         CHN  1982   
63                China         CHN  1983   
64                China         CHN  1984   
65                China         CHN  1985   
66                China         CHN  1986   
67                China         CHN  1987   
68                China         CHN  1988   
69                China         CHN  1989   
70                China         CHN  1990   
71                China         CHN  1991   
72                China         CHN  1992   
73                China         CHN  1993   
74                China         CHN  1994   
75                China         CHN  1995   
76                China         CHN  1996   
77                China         CHN  1997   
78                China         CHN  1998   
79                China         CHN  1999   
80                China         CHN  2000   
81                China         CHN  2001   
82                China         CHN  2002   
83                China         CHN  2003   
84                China         CHN  2004   
85                China         CHN  2005   
86                China         CHN  2006   
87                China         CHN  2007   
88     

In [113]:
# Filling in NaN values by Grouping by the CountryName column and transforming it in order to fillna by specific country mean values
df_master_fill = df_master_filter.groupby('CountryCode').transform(lambda x: x.fillna(x.mean()))
print(f'The shape of the filled dataset: {df_master_fill.shape}')
df_master_fill # I will have to add in the CountryName and CountryCode columns to the combined dataset.

The shape of the filled dataset: (250, 209)


Year  Adjusted savings: carbon dioxide damage (% of GNI)  \
0    1970                                           0.372691    
1    1971                                           0.378426    
2    1972                                           0.379821    
3    1973                                           0.354143    
4    1974                                           0.323506    
5    1975                                           0.328014    
6    1976                                           0.296894    
7    1977                                           0.296063    
8    1978                                           0.313108    
9    1979                                           0.332933    
10   1980                                           0.357798    
11   1981                                           0.333266    
12   1982                                           0.345343    
13   1983                                           0.499338    
14   1984                                           0.524224    
15   1985                                           0.558641    
16   1986                                           0.530679    
17   1987                                           0.529146    
18   1988                                           0.507813    
19   1989                                           0.392948    
20   1990                                           0.408748    
21   1991                                           0.348696    
22   1992                                           0.554267    
23   1993                                           0.562213    
24   1994                                           0.493612    
25   1995                                           0.392491    
26   1996                                           0.415594    
27   1997                                           0.444765    
28   1998                                           0.498555    
29   1999                                           0.776124    
30   2000                                           0.747165    
31   2001                                           0.951648    
32   2002                                           1.080892    
33   2003                                           0.996788    
34   2004                                           0.921713    
35   2005                                           0.754987    
36   2006                                           0.643022    
37   2007                                           0.561133    
38   2008                                           0.519789    
39   2009                                           0.518514    
40   2010                                           0.470395    
41   2011                                           0.434845    
42   2012                                           0.517800    
43   2013                                           0.573253    
44   2014                                           0.644740    
45   2015                                           0.864867    
46   2016                                           0.830430    
47   2017                                           0.781795    
48   2018                                           0.940704    
49   2019                                           0.542946    
50   1970                                           1.382085    
51   1971                                           1.576715    
52   1972                                           1.580489    
53   1973                                           1.464952    
54   1974                                           1.612143    
55   1975                                           1.855925    
56   1976                                           2.235697    
57   1977                                           2.357602    
58   1978                                           3.392944    
59   1979                                           3.245542    
60   1980                               

In [115]:
# In order to add these columns back into the dataframe I used insert to manually do so.
#df_master_fill.insert(0, 'CountryName', df_insert1) # The insert methods must be uncommented to add the two columns to the dataset
#df_master_fill.insert(1, 'CountryCode', df_insert2)
#df_master_fill = df_master_fill.drop('CountryName',axis=1) # this was used to make sure the position of the column was correct
df_master_fill

CountryName CountryCode  Year  \
0                Brazil         BRA  1970   
1                Brazil         BRA  1971   
2                Brazil         BRA  1972   
3                Brazil         BRA  1973   
4                Brazil         BRA  1974   
5                Brazil         BRA  1975   
6                Brazil         BRA  1976   
7                Brazil         BRA  1977   
8                Brazil         BRA  1978   
9                Brazil         BRA  1979   
10               Brazil         BRA  1980   
11               Brazil         BRA  1981   
12               Brazil         BRA  1982   
13               Brazil         BRA  1983   
14               Brazil         BRA  1984   
15               Brazil         BRA  1985   
16               Brazil         BRA  1986   
17               Brazil         BRA  1987   
18               Brazil         BRA  1988   
19               Brazil         BRA  1989   
20               Brazil         BRA  1990   
21               Brazil         BRA  1991   
22               Brazil         BRA  1992   
23               Brazil         BRA  1993   
24               Brazil         BRA  1994   
25               Brazil         BRA  1995   
26               Brazil         BRA  1996   
27               Brazil         BRA  1997   
28               Brazil         BRA  1998   
29               Brazil         BRA  1999   
30               Brazil         BRA  2000   
31               Brazil         BRA  2001   
32               Brazil         BRA  2002   
33               Brazil         BRA  2003   
34               Brazil         BRA  2004   
35               Brazil         BRA  2005   
36               Brazil         BRA  2006   
37               Brazil         BRA  2007   
38               Brazil         BRA  2008   
39               Brazil         BRA  2009   
40               Brazil         BRA  2010   
41               Brazil         BRA  2011   
42               Brazil         BRA  2012   
43               Brazil         BRA  2013   
44               Brazil         BRA  2014   
45               Brazil         BRA  2015   
46               Brazil         BRA  2016   
47               Brazil         BRA  2017   
48               Brazil         BRA  2018   
49               Brazil         BRA  2019   
50                China         CHN  1970   
51                China         CHN  1971   
52                China         CHN  1972   
53                China         CHN  1973   
54                China         CHN  1974   
55                China         CHN  1975   
56                China         CHN  1976   
57                China         CHN  1977   
58                China         CHN  1978   
59                China         CHN  1979   
60                China         CHN  1980   
61                China         CHN  1981   
62                China         CHN  1982   
63                China         CHN  1983   
64                China         CHN  1984   
65                China         CHN  1985   
66                China         CHN  1986   
67                China         CHN  1987   
68                China         CHN  1988   
69                China         CHN  1989   
70                China         CHN  1990   
71                China         CHN  1991   
72                China         CHN  1992   
73                China         CHN  1993   
74                China         CHN  1994   
75                China         CHN  1995   
76                China         CHN  1996   
77                China         CHN  1997   
78                China         CHN  1998   
79                China         CHN  1999   
80                China         CHN  2000   
81                China         CHN  2001   
82                China         CHN  2002   
83                China         CHN  2003   
84                China         CHN  2004   
85                China         CHN  2005   
86                China         CHN  2006   
87                China         CHN  2007   
88     

In [116]:
# Check to see if imputation worked and no null values/duplicated rows
print(f'The shape of the cleaned dataset: {df_master_fill.shape}')
print(f'Check to see if there are duplicated data: {df_master_fill.duplicated().sum()/df_master_fill.shape[0]*100.0} percent')
df_master_fill.isna().sum()

The shape of the cleaned dataset: (250, 211)
Check to see if there are duplicated data: 0.0 percent


CountryName                                                                                                                  0
CountryCode                                                                                                                  0
Year                                                                                                                         0
Adjusted savings: carbon dioxide damage (% of GNI)                                                                           0
Adjusted savings: carbon dioxide damage (current US$)                                                                        0
Adjusted savings: consumption of fixed capital (% of GNI)                                                                    0
Adjusted savings: consumption of fixed capital (current US$)                                                                 0
Adjusted savings: education expenditure (% of GNI)                                                             

The combined dataframe now contains no null values and duplicated columns. I will now read this dataset as a new CSV file in order to make the transition to the next step, EDA.

In [117]:
# Creating a CSV file for the EDA section
df_master_fill.to_csv(r'C:\Users\Jim\Desktop\df_combined.csv')

## Exploratory Data Analysis
With the cleaning finished, I can now perform an EDA in order to find different summary statistics and gain a deeper understanding of the dataset. The next section is under `Capstone Project: BRICS Analysis EDA` notebook.